<a href="https://colab.research.google.com/github/towardsai/ai-tutor-rag-system/blob/main/notebooks/03-RAG_with_LlamaIndex.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Install Packages and Setup Variables

In [1]:
!pip install -q llama-index==0.10.5 openai==1.12.0 cohere==4.47 tiktoken==0.6.0

In [2]:
import os

# Set the "OPENAI_API_KEY" in the Python environment. Will be used by OpenAI client later.
os.environ["OPENAI_API_KEY"] = "<YOUR_OPENAI_KEY>"

# Load Dataset

## Download

The dataset includes several articles from the TowardsAI blog, which provide an in-depth explanation of the LLaMA2 model.

In [3]:
!curl -o ./mini-dataset.json https://raw.githubusercontent.com/AlaFalaki/tutorial_notebooks/main/data/mini-dataset.json

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 25361  100 25361    0     0   195k      0 --:--:-- --:--:-- --:--:--  196k


## Read File

In [4]:
import json

# Load the file as a JSON
with open('./mini-dataset.json', 'r') as file:
    data = json.load(file)

# The number of chunks in the dataset.
len( data['chunks'] )

22

In [5]:
# Flatten the JSON variable to a list of texts.
texts = [item['text'] for item in data['chunks']]

# Generate Embedding

In [6]:
from llama_index.core import Document

# Convert the texts to Document objects so the LlamaIndex framework can process them.
documents = [Document(text=t) for t in texts]

In [7]:
from llama_index.core import VectorStoreIndex

# Build index / generate embeddings using OpenAI.
index = VectorStoreIndex.from_documents(documents, show_progress=True)

/Users/louis/Documents/GitHub/ai-tutor-rag-system/.conda/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Generating embeddings: 100%|██████████| 22/22 [00:00<00:00, 43.01it/s]


In [8]:
# Save the generated embeddings.
# index.storage_context.persist(persist_dir="indexes")

# Query Dataset

In [9]:
from llama_index.llms.openai import OpenAI
# Define a query engine that is responsible for retrieving related pieces of text,
# and using a LLM to formulate the final answer.
llm = OpenAI(temperature=0, model="gpt-3.5-turbo-0125", max_tokens=512)
query_engine = index.as_query_engine(llm=llm)

In [10]:
response = query_engine.query(
    "How many parameters LLaMA2 model has?"
)
print(response)

The Llama 2 model comes in four different sizes: 7 billion, 13 billion, 34 billion, and 70 billion parameters.
